In [76]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [ ]:
import pandas as pd
import numpy as np
import altair as alt
import altair_saver
import glob
import os
import copy
import collections
alt.data_transformers.disable_max_rows()

In [ ]:
def personal():
    return {
        'config': {
            'view': {
                'height': 300,
                'width': 400,
            },
            'range': {
                'category': {'scheme': 'set2'},
                'ordinal': {'scheme': 'set2'},
            },
            'legend': {
                'labelLimit': 0,
            },
            'background': 'white',
            'mark': {
                'clip': True,
            },
            'line': {
                'size': 3,
#                 'opacity': 0.4
            },


        }
    }

def publication():
    colorscheme = 'set2'
    stroke_color = '333'
    title_size = 24
    label_size = 20
    line_width = 5

    return {
        'config': {
            'view': {
                'height': 500,
                'width': 600,
                'strokeWidth': 0,
                'background': 'white',
            },
            'title': {
                'fontSize': title_size,
            },
            'range': {
                'category': {'scheme': colorscheme},
                'ordinal': {'scheme': colorscheme},
            },
            'axis': {
                'titleFontSize': title_size,
                'labelFontSize': label_size,
                'grid': False,
                'domainWidth': 5,
                'domainColor': stroke_color,
                'tickWidth': 3,
                'tickSize': 9,
                'tickCount': 4,
                'tickColor': stroke_color,
                'tickOffset': 0,
            },
            'legend': {
                'titleFontSize': title_size,
                'labelFontSize': label_size,
                'labelLimit': 0,
                'titleLimit': 0,
                'orient': 'top-left',
#                 'padding': 10,
                'titlePadding': 10,
#                 'rowPadding': 5,
                'fillColor': '#ffffff88',
#                 'strokeColor': 'black',
                'cornerRadius': 0,
            },
            'rule': {
                'size': 3,
                'color': '999',
                # 'strokeDash': [4, 4],
            },
            'line': {
                'size': line_width,
#                 'opacity': 0.4
            },
        }
    }

alt.themes.register('personal', personal)
alt.themes.register('publication', publication)
alt.themes.enable('personal')

In [ ]:
import traceback
import json

def load_args(path):
    with open(path + '/args.json') as f:
        args = json.load(f)
    return args

def merge_args(df, args_dict):
    df = df.copy()
    for k, v in args_dict.items():
        df[k] = v
    return df

def load_jobs(pattern, subdir='exploration', root='.', title=None):    
    jobs = glob.glob(f'{root}/results/{subdir}/{pattern}')
    results = []
    for job in jobs:
        try:
            name = os.path.basename(os.path.normpath(job))
            train_data = pd.read_csv(job + '/train.csv')
            train_data['test'] = False
            test_data = pd.read_csv(job + '/test.csv')
            test_data['test'] = True
            data = pd.concat([train_data, test_data], sort=False)
            data['name'] = name
            
            args_dict = load_args(job)
            data = merge_args(data, args_dict)
            
            results.append(data)
        except Exception as e:
            print(e)
    df = pd.concat(results, sort=False)
    if title is None:
        df['title'] = df['name'].str.replace(r'_seed\d', '')
    else:
        df['title'] = title
    return df.reset_index(drop=True)

def load_sac_results(env, task):
    sac_results = pd.read_csv('results/sac.csv')
    sac_results = sac_results[sac_results.env == f'{env}_{task}']
    sac_results['test'] = True
    sac_results['score'] = sac_results['episode_reward']
    sac_results['name'] = 'SAC'
    sac_results['title'] = 'SAC'
    return sac_results

In [ ]:
INCLUDE_FIELDS = {
    'name', 'title', 'test', 'episode', 'score', 'novelty_score',
}

SidecarChart = collections.namedtuple('SidecarChart', ['chart', 'included_fields'])

def strip_columns(chart, included_fields):
    included_fields.discard(None)
    included_fields = {f.rsplit(':')[0] for f in included_fields}
    df = chart.data
    if isinstance(df, pd.DataFrame):
        chart.data = df.loc[:, df.columns.isin(included_fields)]
    return chart


def plot_with_bars(base_chart, y_col, test, extent='ci', included_fields=set(), strip=True, **kwargs):
    if isinstance(base_chart, SidecarChart):
        base_chart, chart_includes = base_chart
        included_fields = included_fields.union(chart_includes)
    included_fields = included_fields.union({y_col})
    
    legend_chart = base_chart.mark_circle(size=0, opacity=1).encode(
        y=f'mean({y_col}):Q',
        **kwargs
    ).transform_filter(alt.datum.test == test)
    mean_chart = base_chart.encode(
        y=f'mean({y_col}):Q',
        **kwargs
    ).transform_filter(alt.datum.test == test)
    err_chart = base_chart.encode(
        y=f'{y_col}:Q'
    ).transform_filter(alt.datum.test == test).mark_errorband(extent=extent)
    
    chart = legend_chart + err_chart + mean_chart
    title_flag = ' [test]' if test else ' [train]'
    chart.title = base_chart.title + title_flag
    if strip:
        return strip_columns(chart, included_fields)
    return chart


def make_base_chart(data, title, window=5, **kwargs):
    chart = alt.Chart(data, title=title).mark_line().encode(
        x=alt.X('episode', title='Episode'),
        **kwargs
    ).transform_calculate(
        has_score=(alt.datum.score > 0.1),
    ).transform_window(
        sum_novelty='sum(novelty_score)',
        frame=[None, 0],
        groupby=['name', 'test'],
        sort=[{'field': 'episode', 'order': 'ascending'}],
    ).transform_window(
        sum_score='sum(score)',
        frame=[None, 0],
        groupby=['name', 'test'],
        sort=[{'field': 'episode', 'order': 'ascending'}],
    ).transform_window(
        count_score='sum(has_score)',
        frame=[None, 0],
        groupby=['name', 'test'],
        sort=[{'field': 'episode', 'order': 'ascending'}],
    ).transform_window(
        rolling_mean_score='mean(score)',
        frame=[-window, 0],
        groupby=['name', 'test'],
        sort=[{'field': 'episode', 'order': 'ascending'}]
    ).transform_window(
        rolling_mean_novelty='mean(novelty_score)',
        frame=[-window, 0],
        groupby=['name', 'test'],
        sort=[{'field': 'episode', 'order': 'ascending'}],
    ).transform_calculate(
        smoothed_score=((alt.datum.name == 'SAC') * alt.datum.score + 
                        (alt.datum.name != 'SAC') * alt.datum.rolling_mean_score)
    )
    dd_kwargs = collections.defaultdict(lambda: None)
    dd_kwargs.update(**kwargs)
    used_fields = {
        dd_kwargs['color'], 
        dd_kwargs['opacity'], 
        dd_kwargs['shape'],
        dd_kwargs['y'],
    }
    included_fields = INCLUDE_FIELDS.union(used_fields)
    return SidecarChart(chart, included_fields)

In [220]:
alt.themes.enable('personal')
jobs = [
    load_jobs('hallway_v2*', subdir='exploration'),
#     load_jobs('hallway_v2*velocity_1*no_explorationTrue', subdir='exploration', title="SAC velocity 1"),
#     load_jobs('hallway_v2*velocity_4*no_explorationTrue', subdir='exploration', title="SAC velocity 4"),
#     load_jobs('hallway_v2*no_explorationFalse', subdir='exploration'),
#     load_jobs('hallway_v3*', subdir='exploration'),
]
data = pd.concat(jobs, sort=False)

N = 1000
subset = data
# subset = subset[((subset.episode % 5 == 0) & (subset.test)) | ((subset.episode % 3 == 0) & (~subset.test))]
subset = subset[(subset['episode'] <= N)]
chart = make_base_chart(
    subset, 
    title="Hallway", 
    opacity='use_exploration',
    color='task',
#     color='name',
    window=0,
)

(plot_with_bars(chart, 'rolling_mean_score', test=False) | plot_with_bars(chart, 'smoothed_score', test=True)) & \
(plot_with_bars(chart, 'sum_novelty', test=False) | plot_with_bars(chart, 'count_score', test=False)) & \
(plot_with_bars(chart, 'policy_entropy', test=False))
# (plot_with_bars(chart, 'elapsed', test=False) | plot_with_bars(chart, 'density_size', test=False))

alt.VConcatChart(...)

In [205]:
alt.themes.enable('personal')
jobs = [
    load_jobs('hallway_distractor_v1*no_explorationTrue*', subdir='exploration', title="SAC"),
    load_jobs('hallway_distractor_v1*no_explorationFalse*', subdir='exploration'),
    load_jobs('hallway_distractor_v2*', subdir='exploration'),
]
data = pd.concat(jobs, sort=False)

N = 1000
subset = data
# subset = subset[((subset.episode % 5 == 0) & (subset.test)) | ((subset.episode % 3 == 0) & (~subset.test))]
subset = subset[(subset['episode'] <= N)]
chart = make_base_chart(
    subset, 
    title="Hallway distractor", 
#     opacity='use_exploration',
#     color='task',
    color='title',
    window=0,
)

(plot_with_bars(chart, 'rolling_mean_score', test=False) | plot_with_bars(chart, 'smoothed_score', test=True)) & \
(plot_with_bars(chart, 'sum_novelty', test=False) | plot_with_bars(chart, 'count_score', test=False)) & \
(plot_with_bars(chart, 'policy_entropy', test=False))
# (plot_with_bars(chart, 'elapsed', test=False) | plot_with_bars(chart, 'density_size', test=False))

alt.VConcatChart(...)

In [247]:
alt.themes.enable('personal')
jobs = [
    load_jobs('hallway_v4*seed0*', subdir='exploration'),
]
data = pd.concat(jobs, sort=False)

N = 300
subset = data
subset = subset[(subset['episode'] <= N)]
subset = subset[subset.test == False]
entropy_chart = alt.Chart(subset).mark_line(stroke='green').encode(
    x='episode',
    y=alt.Y('policy_entropy', axis=alt.Axis(titleColor='green')),
    detail='name',
)
alpha_chart = alt.Chart(subset).mark_line(stroke='blue').encode(
    x='episode',
    y=alt.Y('alpha', scale=alt.Scale(type='log'), axis=alt.Axis(titleColor='blue')),
    detail='name',
)
(entropy_chart + alpha_chart).resolve_scale(y='independent')

alt.LayerChart(...)

In [266]:
alt.themes.enable('personal')
jobs = [
    load_jobs('reacher_explore_v3*', subdir='exploration'),
]
data = pd.concat(jobs, sort=False)

N = 1000
subset = data
# subset = subset[((subset.episode % 5 == 0) & (subset.test)) | ((subset.episode % 3 == 0) & (~subset.test))]
subset = subset[(subset['episode'] <= N)]
chart = make_base_chart(
    subset, 
    title="Reacher Explore", 
    color='task',
    opacity='use_exploration',
    window=20,
)

# plot_with_bars(chart, 'elapsed', test=False) | plot_with_bars(chart, 'density_size', test=False)
(plot_with_bars(chart, 'rolling_mean_score', test=False) | plot_with_bars(chart, 'smoothed_score', test=True)) & \
(plot_with_bars(chart, 'sum_novelty', test=False) | plot_with_bars(chart, 'count_score', test=False)) & \
(plot_with_bars(chart, 'policy_entropy', test=False))
# (plot_with_bars(chart, 'elapsed', test=False) | plot_with_bars(chart, 'density_size', test=False))


alt.VConcatChart(...)

In [263]:
alt.themes.enable('personal')
jobs = [
# #     load_jobs('arxiv2_pv100_seed*', subdir='exploration', title='arxiv results'),
#     load_jobs('arxiv2_pv100_seed*', subdir='exploration', title='arxiv UFO'),
#     load_jobs('arxiv2_pv100_noopt_seed*', subdir='exploration', title='arxiv UF'),
#     load_jobs('arxiv2_pv100_slow_seed*', subdir='slow', title='arxiv U'),
#     load_jobs('arxiv2_pv100_intrinsic_seed*', subdir='intrinsic', title='arxiv BBE'),
#     load_jobs('arxiv2_pv100_noexplore_seed*', subdir='exploration', title='arxiv undirected'),
# #     load_jobs('epv100kcdiag_sscale0.01_ascale1*', subdir='exploration', title='q policy small kernel'),
# #     load_jobs('epv100kcdiag_sscale0.1_ascale1*', subdir='exploration', title='q policy large kernel'),
#     load_jobs('pv100_sac', subdir='exploration', title='sacxploration seed 1'),
#     load_jobs('pv100_sac_seed2', subdir='exploration', title='sacxploration seed 2'),
    
#     load_jobs('pv100_sac_sscale0.01', subdir='exploration', title='sacxploration small kernel'),
#     load_jobs('pv100_sac_2x_no_exploration*', subdir='exploration'),
#     load_jobs('pv100_sac_2x_uniform*', subdir='exploration'),
#     load_jobs('pv100_sac_2x_warm500*', subdir='exploration'),
    
    load_jobs('pv100_sac_2x_no_explorationTrue', subdir='exploration', title='SAC'),
#     load_jobs('pv100_sac_2x_warm500_uniform_update_candidatesTrue', subdir='exploration', title='SAC + exploration'),
    
#     load_jobs('pv100_check_tol*', subdir='exploration'),
#     load_jobs('pv100_updates*', subdir='exploration'),
#     load_jobs('pv100_500_updates_n*', subdir='exploration'),
    load_jobs('pv100_check_seed*', subdir='exploration'),
    load_jobs('pv100_keops_v3*', subdir='exploration'),

]
data = pd.concat(jobs, sort=False)

N = 1000
subset = data
# subset = subset[((subset.episode % 5 == 0) & (subset.test)) | ((subset.episode % 3 == 0) & (~subset.test))]
subset = subset[(subset['episode'] <= N)]
chart = make_base_chart(
    subset, 
    title="Point Velocity", 
    color='title',
    window=10,
)

# plot_with_bars(chart, 'elapsed', test=False) | plot_with_bars(chart, 'density_size', test=False)
(plot_with_bars(chart, 'rolling_mean_score', test=False) | plot_with_bars(chart, 'smoothed_score', test=True)) & \
(plot_with_bars(chart, 'sum_novelty', test=False) | plot_with_bars(chart, 'count_score', test=False)) & \
(plot_with_bars(chart, 'elapsed', test=False) | plot_with_bars(chart, 'density_size', test=False))
# (plot_with_bars(chart, 'policy_entropy', test=False))

alt.VConcatChart(...)

In [ ]:
alt.themes.enable('personal')
jobs = [
#     load_sac_results('hopper', 'hop'),
    load_jobs('hopper_sac_noexplore*', subdir='exploration', root='/home/will/vlg4/exploration-reimplement', title='SAC'),

#     load_jobs('hopper_sac_2x_density_state_scale1*', subdir='exploration'),
#     load_jobs('hopper_sac2x_uniform*', subdir='exploration'),
#     load_jobs('hopper_sac_max8192_seed2*', subdir='exploration'),
#     load_jobs('hopper_sac_max8192_density_state_scale1*', subdir='exploration', root='/home/will/vlg4/exploration-reimplement'),

#     load_jobs('hopper_sizes*', subdir='exploration', root='/home/will/vlg4/exploration-reimplement'),
#     load_jobs('hopper_speedy_sizes*', subdir='exploration', root='/home/will/vlg4/exploration-reimplement'),
    
    
    load_jobs('hopper_keops*', subdir='exploration', root='/home/will/vlg4/exploration-reimplement'),
    load_jobs('hopper_keops*', subdir='exploration'),
]
data = pd.concat(jobs, sort=False)

N = 1000
subset = data
# subset = subset[((subset.episode % 5 == 0) & (subset.test)) | (((subset.episode - 3) % 5 == 0) & (~subset.test))]
subset = subset[(subset['episode'] <= N)]
chart = make_base_chart(
    subset, 
    title="Hopper Hop", 
    color='title',
    window=20,
)

(plot_with_bars(chart, 'rolling_mean_score', test=False) | plot_with_bars(chart, 'smoothed_score', test=True)) & \
(plot_with_bars(chart, 'sum_novelty', test=False) | plot_with_bars(chart, 'count_score', test=False)) & \
(plot_with_bars(chart, 'elapsed', test=False) | plot_with_bars(chart, 'density_size', test=False))

In [ ]:
alt.themes.enable('personal')
jobs = [
    load_jobs('manipulator_v5*', subdir='exploration', root='/home/will/vlg4/exploration-reimplement'),
    load_jobs('manipulator_keops_v3*', subdir='exploration', root='/home/will/vlg4/exploration-reimplement'),
    load_jobs('manipulator_keops_v4*', subdir='exploration', root='/home/will/vlg4/exploration-reimplement'),
]
data = pd.concat(jobs, sort=False)

N = 10000
subset = data
# subset = subset[((subset.episode % 5 == 0) & (subset.test)) | ((subset.episode % 3 == 0) & (~subset.test))]
subset = subset[(subset['episode'] <= N)]
chart = make_base_chart(
    subset, 
    title="manipulator bring_ball", 
    color='title',
    window=20,
)

(plot_with_bars(chart, 'rolling_mean_score', test=False) | plot_with_bars(chart, 'smoothed_score', test=True)) & \
(plot_with_bars(chart, 'policy_entropy', test=False) | plot_with_bars(chart, 'count_score', test=False)) & \
(plot_with_bars(chart, 'elapsed', test=False) | plot_with_bars(chart, 'density_size', test=False))

In [ ]:
alt.themes.enable('personal')
jobs = [
    load_sac_results('acrobot', 'swingup'),   
    load_jobs('acrobot_swingup', subdir='exploration', root='/home/will/vlg4/exploration-reimplement',
              title='acrobot swingup, kernel scale 0.3'),
]
data = pd.concat(jobs, sort=False)

N = 1000
subset = data
# subset = subset[((subset.episode % 5 == 0) & (subset.test)) | ((subset.episode % 3 == 0) & (~subset.test))]
subset = subset[(subset['episode'] <= N)]
chart = make_base_chart(
    subset, 
    title="Acrobot Swingup", 
    color='title',
    window=30,
)


(plot_with_bars(chart, 'rolling_mean_score', test=False) | plot_with_bars(chart, 'smoothed_score', test=True)) & \
(plot_with_bars(chart, 'sum_novelty', test=False) | plot_with_bars(chart, 'count_score', test=False)) & \
(plot_with_bars(chart, 'policy_entropy', test=False)) &\
(plot_with_bars(chart, 'elapsed', test=False).interactive() | plot_with_bars(chart, 'density_size', test=False).interactive())

In [ ]:
alt.themes.enable('personal')
jobs = [
#     load_jobs('ecpkcdiagfix_sscale*', subdir='exploration'),
#     load_jobs('ecpkcdiagfix_plr*', subdir='exploration'),
#     load_jobs('ecpkcdiagfix_plr1e-4_sscale0.1_ascale1*', subdir='exploration'),
    load_jobs('ecp_tab_20x2*', subdir='exploration', title='tabular count'),
#     load_jobs('cp_noexplore*', subdir='exploration', title='no exploration'),
    load_sac_results('cartpole', 'swingup_sparse'),   
    load_jobs('ecp_kcweight_plr1e-4_sscale0.1*', subdir='exploration'),


    load_jobs('cart_temp_policy_temperature0.1*', subdir='exploration'),

    load_jobs('cart_sac_2x*', subdir='exploration'),
    
#     load_jobs('cart_approx*', subdir='exploration'),
#     load_jobs('cart_temp*', subdir='exploration'),
#     load_jobs('cart_sac', subdir='exploration'),

]
data = pd.concat(jobs, sort=False)

N = 300
subset = data
# subset = subset[((subset.episode % 5 == 0) & (subset.test)) | ((subset.episode % 3 == 0) & (~subset.test))]
subset = subset[(subset['episode'] <= N)]
chart = make_base_chart(
    subset, 
    title="Cartpole Swingup (sparse)", 
    color='title',
    window=10,
)

(plot_with_bars(chart, 'rolling_mean_score', test=False) | plot_with_bars(chart, 'smoothed_score', test=True)) & \
(plot_with_bars(chart, 'sum_novelty', test=False) | plot_with_bars(chart, 'count_score', test=False)) & \
(plot_with_bars(chart, 'policy_entropy', test=False) | plot_with_bars(chart, 'policy_entropy', test=True))

In [ ]:
alt.themes.enable('personal')
jobs = [
    load_jobs('gw20_tab*', subdir='exploration', title='tabular count'),
    load_jobs('gw20_sscale*', subdir='exploration', title='kernel count (tiny)'),
    load_jobs('gw20fixedkernel_sscale0.001*', subdir='exploration', title='kernel count (tiny, fixed)'),
    load_jobs('gw20fixedkernel_sscale0.1*', subdir='exploration', title='kernel count (medium, fixed)'),
]
data = pd.concat(jobs, sort=False)
N = 100
subset = data
# subset = subset[((subset.episode % 5 == 0) & (subset.test)) | ((subset.episode % 3 == 0) & (~subset.test))]
subset = subset[(subset['episode'] <= N)]
chart = make_base_chart(
    subset, 
    title="Gridworld 20x20", 
    color='title',
    window=5,
)

(plot_with_bars(chart, 'rolling_mean_score', test=False) | plot_with_bars(chart, 'smoothed_score', test=True)) & \
(plot_with_bars(chart, 'sum_novelty', test=False).interactive() | plot_with_bars(chart, 'count_score', test=False)) & \
plot_with_bars(chart, 'policy_entropy', test=True)

In [ ]:
alt.themes.enable('personal')
jobs = [
    load_jobs('arxiv2_pv100_seed*', subdir='exploration', title='tabular_density'),
#     load_jobs('explore_pv100_kcount*', subdir='exploration'),
#     load_jobs('explore_pv100_k*clippednum*', subdir='exploration'),
#     load_jobs('epv100kc_scale*', subdir='exploration'),
#     load_jobs('epv100kc_sscale*', subdir='exploration'),
#     load_jobs('epv100kcfix_sscale*', subdir='exploration'),
#     load_jobs('epv100kcrefix_sscale*', subdir='exploration'),
    load_jobs('epv100kcdiag_sscale*', subdir='exploration'),
]
data = pd.concat(jobs, sort=False)
N = 200
subset = data
# subset = subset[((subset.episode % 5 == 0) & (subset.test)) | ((subset.episode % 3 == 0) & (~subset.test))]
subset = subset[(subset['episode'] <= N)]
chart = make_base_chart(
    subset, 
    title="Point Velocity", 
    color='title',
    window=5,
)

(plot_with_bars(chart, 'rolling_mean_score', test=False) | plot_with_bars(chart, 'smoothed_score', test=True)) & \
(plot_with_bars(chart, 'sum_novelty', test=False) | plot_with_bars(chart, 'count_score', test=False)) & \
plot_with_bars(chart, 'policy_entropy', test=True)

In [ ]:
alt.themes.enable('personal')
env = 'reacher'
task = 'hard'
jobs = [
    load_sac_results(env, task),
]
data = pd.concat(jobs, sort=False)

subset = data
subset = subset[(subset['episode'] <= 1000)]
chart = make_base_chart(
    subset, 
    title=f"{env} {task}", 
    color='name')

chart = plot_with_bars(chart, 'rolling_mean_score', test=True)
# chart.encode(y='mean(score').interactive()
chart.interactive()


In [ ]:
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

def plot(df, base=None, key='episode_reward'):
    envs = np.sort(df.env.unique())
    ncol = 3
    assert envs.shape[0] % ncol == 0
    nrow = envs.shape[0] // ncol
    fig, axs = plt.subplots(nrow, ncol, figsize=(4 * ncol, 3 * nrow))
    #runs = sorted([str(x) for x in df.run.unique()])
    for idx, env in enumerate(envs):
        data = df[df['env'] == env]
        row = idx // ncol
        col = idx % ncol
        ax = axs[row, col]
        hue_order = np.sort(data.Agent.unique())
        #import ipdb; ipdb.set_trace()
        sns.lineplot(x='step', y=key, data=data, ci='sd', hue='Agent', hue_order=hue_order, ax=ax)
        #sns.lineplot(x=‘step’, y=key, data=data, ci=‘sd’, hue=‘run_id’, ax=ax, palette=sns.color_palette(‘Blues’)[3:4])
        if base is not None:
            if env in base:
                val = base[env]['d4pg']
                ax.axhline(val, ls='--', color='black', label='D4PG ($10^8$ steps)')
                ax.legend()
        ax.set_title(f'{env}')
        #ax.set_xlim(0, 10000000)
        #ax.set_ylim(0.0, 1050.0)
        #ax.legend_.remove()
    plt.tight_layout()
    plt.show()
plot(pd.read_csv('results/sac.csv'))

In [ ]:
alt.themes.enable('personal')
jobs = [
    load_sac_results('cheetah', 'run'),   
#     load_jobs('acrobot_sac*', subdir='exploration', root='/home/will/vlg4/exploration-reimplement'),
]
data = pd.concat(jobs, sort=False)

N = 1000
subset = data
# subset = subset[((subset.episode % 5 == 0) & (subset.test)) | ((subset.episode % 3 == 0) & (~subset.test))]
subset = subset[(subset['episode'] <= N)]
chart = make_base_chart(
    subset, 
    title="cheetah run", 
    color='title',
    window=10,
)

plot_with_bars(chart, 'smoothed_score', test=True)